<div class="alert alert-success alertinfo" style="margin-top: 0px">
<h1>  Model 1. Collaborative filtering </h1>  
</div>

<font size="4"> 
    Since we are dealing with implicit data we’re going to write an implicit recommendation algorithm using collaborative filtering approach. What it means is that we will only be concern ourselves with the games, users and which games a user has interacted with. </font>  

# 1. Imports

In [1]:
# Turning off warnings
import warnings
warnings.filterwarnings('ignore')

In [2]:
import sys
import random
import pandas as pd
import numpy as np

import scipy.sparse as sparse
from scipy.sparse.linalg import spsolve
from sklearn.preprocessing import MinMaxScaler

import implicit

In [3]:
# Import data
train = pd.read_csv(r"C:\Users\giuse\Desktop\job seeking\DATAscience_interview\train_modelled.csv")
test = pd.read_csv(r"C:\Users\giuse\Desktop\job seeking\DATAscience_interview\test_modelled.csv")

# 2. Data view

In [4]:
# Data info
print('In train set there are:')
print('             {} rows and {} columns.'.format(train.shape[0],train.shape[1]))
print('             {} unique users.'.format(len(train['USER_ID'].unique())))
print('             {} unique game titles.'.format(len(train['GAME_TITLE'].unique())))

print('------------------------------------------')
print('In test set there are:')
print('            {} rows and {} columns.'.format(test.shape[0],test.shape[1]))
print('            {} unique users.'.format(len(test['USER_ID'].unique())))
print('            {} unique game titles.'.format(len(test['GAME_TITLE'].unique())))

In train set there are:
             787487 rows and 13 columns.
             39326 unique users.
             2569 unique game titles.
------------------------------------------
In test set there are:
            196872 rows and 13 columns.
            24660 unique users.
            2446 unique game titles.


# 3. Methodology

## 3a Feature selection

<font size="4">
As mentiod before we only need interactions between user-item and our implicit feedback (taken from bet count).</font>

In [5]:
# Chosen features
features = ['USER_ID','USER_CODE','GAME_TITLE','GAME_CODE','FEEDBACK']

In [6]:
# Selecting features
train = train[features]
test = test[features]
train.head()

USER_ID  USER_CODE         GAME_TITLE  GAME_CODE  FEEDBACK
0        1          0        Slotomon Go       2027        -1
1        5          1          Starburst       2085        -1
2      181          2      Stellar Spins       2096         2
3     1939          3  Show me the Mummy       1992         2
4     6784          4    Wild Diamond 7x       2475        -1

<font size="4">
What we are trying to do here, is to create a matrix of users versus items(games). This will create a very large but sparse matrix. Please note that we have more than 2500 games to our disposal but even most active players had interactions with only small sample of them. So this matrix will consists mainly of zeroes and occasional 'interaction' given as implicit feedback</font>

## 3b Matrix factorization  

<font size="4">
    When we talk about collaborative filtering for recommender systems we want to solve the problem of our original matrix having thousands of different dimensions, but our “tastes” are not being nearly as complex. Here we can actually use matrix factorization to mathematically reduce the dimensionality of our original “all users by all games” matrix into something much smaller that represents “all games by some taste dimensions” and “all users by some taste dimensions”. These dimensions are called latent or hidden features and we learn them from our data.
Doing this reduction and working with fewer dimensions makes it both much more computationally efficient</font>

![alt text](matrix_factorization.png)

# 4. Fitting the model

In [7]:
# The implicit library expects data as a item-user matrix so we
# create two matricies, one for fitting the model (game-user) 
# and one for recommendations (user-game)
sparse_game_user = sparse.csr_matrix((train['FEEDBACK'].astype(float), (train['GAME_CODE'], train['USER_CODE'])))
sparse_user_game = sparse.csr_matrix((train['FEEDBACK'].astype(float), (train['USER_CODE'], train['GAME_CODE'])))

In [8]:
# Initialize the als model and fit it using the sparse item-user matrix
model = implicit.als.AlternatingLeastSquares(factors=20, regularization=0.1, iterations=20)

# Calculate the confidence by multiplying it by our alpha value.
alpha_val = 15
data_conf = (sparse_game_user * alpha_val).astype('double')

#Fit the model
model.fit(data_conf)

In [9]:
model

# Finding similar games

In [12]:
# Finding the n most similar games to
game_name = 'Stellar Spins'
n_similar = 3

In [14]:
# get game code
game_code = int(test.GAME_CODE.loc[test.GAME_TITLE == game_name].iloc[0])

# Use implicit to get similar items.
similar = model.similar_items(game_code, n_similar+1)

# Print the names of our most similar games
for item in similar:
    idx, score = item
    if train.GAME_TITLE.loc[train.GAME_CODE == idx].iloc[0] != game_name:
        print(train.GAME_TITLE.loc[train.GAME_CODE == idx].iloc[0])

Atlantic City Blackjack Gold
Wild Plunder
Loot a fruit


In [15]:
# get game code
#game_code = int(test.GAME_CODE.loc[test.GAME_TITLE == game_name].iloc[0])

# Use implicit to get similar items.
#similar = model.similar_items(game_code, n_similar+1)

# Print the names of our most similar games
#for item in similar:
#    idx, score = item
#    if test.GAME_TITLE.loc[test.GAME_CODE == idx].iloc[0] != game_name:
#        print(test.GAME_TITLE.loc[test.GAME_CODE == idx].iloc[0])

# Making recommendations

In [16]:
# Finding n recommendation for users
number_of_recommendations = 3
test_users = test['USER_ID'].unique()
test_users

array([      5,     181,    1939, ..., 2583350, 2583538, 2583547],
      dtype=int64)

In [17]:
for i in test_users:
    # get user_code
    user_code = int(test.USER_CODE.loc[test.USER_ID == i].iloc[0])
    # Use the implicit recommender.
   
    recommended = model.recommend(user_code, sparse_user_game)

    games = []
    scores = []

    # Get game names from ids
    for item in recommended:
        idx, score = item
        games.append(test.GAME_TITLE.loc[test.GAME_CODE == idx].iloc[0])
        scores.append(score)

    # Create a dataframe of games names and scores
    recommendations = pd.DataFrame({'games': games, 'score': scores})
    recommendations = recommendations.head(number_of_recommendations)
    print('Recommendations for user number {}'.format(i))
    print(recommendations)
    print('-------------')

Recommendations for user number 5
           games         score
0  Book of Egypt  1.029254e-11
1   Demi Gods II  9.300088e-12
2  Wolf Treasure  8.409347e-12
-------------
Recommendations for user number 181
           games     score
0  Book of Egypt  1.027502
1   Book of Dead  0.969918
2    Bison Trail  0.961466
-------------
Recommendations for user number 1939
            games     score
0       Wolf Gold  0.503781
1  Ancient Giants  0.499822
2    Disco Bar 7s  0.412284
-------------
Recommendations for user number 20348
               games         score
0          Wolf Gold  1.855938e-11
1       Disco Bar 7s  5.286532e-12
2  Feng Shui Kitties  5.069582e-12
-------------
Recommendations for user number 20990
                games     score
0  Legend of Atlantis  0.997315
1     Satoshis Secret  0.942464
2        Book of Dead  0.788185
-------------
Recommendations for user number 21078
          games     score
0  Diamond Cats  0.924442
1        Pimped  0.922519
2    Hot Choice  0.

Recommendations for user number 130371
                  games     score
0       Wild Diamond 7x  1.268005
1  Ultimate Super Reels  0.864478
2           Wild Respin  0.817919
-------------
Recommendations for user number 133442
            games     score
0  Lucky Streak 3  0.746533
1  Lucky Streak 2  0.698666
2     Lucky Seven  0.653389
-------------
Recommendations for user number 164527
             games     score
0      Bison Trail  1.059938
1  Booming Bananas  0.938930
2    Wolf Treasure  0.917176
-------------
Recommendations for user number 170192
                games         score
0      Fire Lightning  1.103518e-11
1       Wolf Treasure  9.496556e-12
2  Aztec Magic Deluxe  9.209214e-12
-------------
Recommendations for user number 174026
          games     score
0  Book of Dead  0.719094
1  Ancient Troy  0.622843
2        Voodoo  0.611935
-------------
Recommendations for user number 174304
            games     score
0     Rocket Dice  0.935658
1  Rook's Revenge  0.911586


Recommendations for user number 301988
                games     score
0        Demi Gods II  0.889248
1  Aztec Magic Deluxe  0.778819
2      Dragon Kingdom  0.749131
-------------
Recommendations for user number 333925
                games     score
0        Book of Dead  0.836912
1  Legend of Atlantis  0.689406
2        Dragon Wilds  0.678656
-------------
Recommendations for user number 334114
                                  games     score
0                          Book of Dead  1.147499
1                       Rise of Olympus  1.069900
2  Siren’s Treasures II 15 Lines Series  1.014329
-------------
Recommendations for user number 334136
            games     score
0    Mustang Gold  0.439519
1    Demi Gods II  0.421093
2  Speed Roulette  0.392043
-------------
Recommendations for user number 334935
                games     score
0  Platinum Lightning  0.331263
1     Booming Bananas  0.261007
2            Roulette  0.216676
-------------
Recommendations for user number 338957


2      Bonanza  5.454183e-12
-------------
Recommendations for user number 445723
            games     score
0   Book of Egypt  1.124457
1  Dragon Kingdom  0.827137
2      Mega Drago  0.740495
-------------
Recommendations for user number 446281
          games     score
0  Book of Dead  0.519742
1      Hot Spin  0.328083
2  Wild Diamond  0.291138
-------------
Recommendations for user number 447126
            games     score
0  Rise of Merlin  0.707598
1  Madame Destiny  0.627985
2   Sweet Bonanza  0.627073
-------------
Recommendations for user number 447737
                games     score
0        Demi Gods II  0.573220
1  Aztec Magic Deluxe  0.493011
2     Booming Bananas  0.466979
-------------
Recommendations for user number 447900
           games     score
0      Eye Of Ra  0.735497
1  Book Of Aztec  0.718503
2    Jade Valley  0.692416
-------------
Recommendations for user number 448058
             games     score
0   Fire Lightning  0.751261
1        Starburst  0.626681
2 

Recommendations for user number 464234
           games     score
0    Billyonaire  1.157786
1    Jade Valley  1.127171
2  Fruits Deluxe  1.043748
-------------
Recommendations for user number 464972
               games     score
0  88 Lucky Fortunes  0.188302
1      Majestic King  0.183549
2     Chinese Tigers  0.167086
-------------
Recommendations for user number 465229
                     games     score
0            Blackjack VIP  0.639800
1              Lucky Seven  0.608762
2  Multihand Blackjack Pro  0.572807
-------------
Recommendations for user number 465747
                     games     score
0              Jade Valley  0.780109
1                Wolf Gold  0.762024
2  Multihand Blackjack Pro  0.680828
-------------
Recommendations for user number 465769
                 games         score
0       Fire Lightning  1.563388e-11
1   Aztec Magic Deluxe  1.517937e-11
2  Lucky Lady's Clover  1.280263e-11
-------------
Recommendations for user number 465779
               games

...

Recommendations for user number 2559465
                games     score
0  Aztec Magic Deluxe  0.448128
1       Wolf Treasure  0.447388
2           Wolf Gold  0.397684
-------------
Recommendations for user number 2559489
            games     score
0     Rocket Dice  0.380430
1       Fruit Zen  0.380342
2  Rook's Revenge  0.337285
-------------
Recommendations for user number 2559666
                           games         score
0                 Lucky Streak 1  2.838777e-12
1                       Roulette  2.741550e-12
2  Demi Gods II-Expanded Edition  2.695030e-12
-------------
Recommendations for user number 2559710
                games     score
0    Speed Baccarat B  0.415392
1   European Roulette  0.392674
2  Platinum Lightning  0.367845
-------------
Recommendations for user number 2559810
                games     score
0  Legend of Atlantis  0.286297
1       Boomshakalaka  0.266482
2           Lucky Cat  0.245573
-------------
Recommendations for user number 2559881
      

Recommendations for user number 2565306
              games     score
0   Booming Bananas  0.548330
1  Domnitors Deluxe  0.483736
2         West Town  0.480791
-------------
Recommendations for user number 2565436
                     games     score
0  Multihand Blackjack Pro  0.399067
1              Jade Valley  0.396247
2                West Town  0.384812
-------------
Recommendations for user number 2565546
               games     score
0          Lucky Cat  0.382512
1       Super Sevens  0.270572
2  Caishen's Fortune  0.249004
-------------
Recommendations for user number 2565671
              games     score
0  Pharaoh's Empire  0.499380
1     Wolf Treasure  0.467951
2      Mustang Gold  0.452776
-------------
Recommendations for user number 2565675
                  games     score
0       Wild Diamond 7x  0.535591
1       Booming Bananas  0.411228
2  Booming Seven Deluxe  0.313043
-------------
Recommendations for user number 2565747
                 games         score
0    

Recommendations for user number 2569565
               games         score
0  European Roulette  3.010239e-12
1      Blackjack VIP  2.732717e-12
2  American Roulette  2.636589e-12
-------------
Recommendations for user number 2569590
           games     score
0  Blackjack VIP  0.380035
1     Hot 4 Cash  0.332530
2   Aztec Palace  0.301128
-------------
Recommendations for user number 2569639
                games     score
0       Boomshakalaka  0.343652
1  Legend of Atlantis  0.289073
2           Lucky Cat  0.277787
-------------
Recommendations for user number 2569680
                games         score
0      Fire Lightning  1.167199e-11
1  Platinum Lightning  1.038673e-11
2  Aztec Magic Deluxe  9.620763e-12
-------------
Recommendations for user number 2569691
            games     score
0  Chinese Tigers  0.935986
1       Lucky Cat  0.878404
2  The Moneymania  0.651467
-------------
Recommendations for user number 2569890
                games     score
0           Wolf Gold  0.3

Recommendations for user number 2575055
             games     score
0        Reactoonz  0.787461
1  Rise of Olympus  0.722254
2     Perfect Gems  0.658728
-------------
Recommendations for user number 2575103
                games         score
0  Aztec Magic Deluxe  1.882124e-11
1         Aztec Magic  1.314868e-11
2  Platinum Lightning  1.269608e-11
-------------
Recommendations for user number 2575117
          games     score
0  Diamond Cats  0.571533
1     Lucky Cat  0.536878
2   Billyonaire  0.509709
-------------
Recommendations for user number 2575127
          games         score
0  Book of Dead  5.392250e-12
1   Bison Trail  4.926065e-12
2   Great Ocean  4.469593e-12
-------------
Recommendations for user number 2575280
             games     score
0  Wild Diamond 7x  0.998087
1   Lucky Streak 3  0.854650
2     Demi Gods II  0.765246
-------------
Recommendations for user number 2575410
                games         score
0           Wolf Gold  5.250060e-12
1   Power Of Posei

Recommendations for user number 2579987
                games         score
0      Fire Lightning  1.125002e-11
1  Aztec Magic Deluxe  1.079903e-11
2       Wolf Treasure  8.801375e-12
-------------
Recommendations for user number 2580252
                games         score
0      Fire Lightning  2.044027e-11
1  Aztec Magic Deluxe  1.756067e-11
2       Wolf Treasure  1.280183e-11
-------------
Recommendations for user number 2580254
                games     score
0        Book of Dead  0.294878
1      Jumbo Stampede  0.203991
2  Lightning Roulette  0.201872
-------------
Recommendations for user number 2580327
                games         score
0     Booming Bananas  1.301896e-11
1      Fire Lightning  1.261276e-11
2  Aztec Magic Deluxe  9.344330e-12
-------------
Recommendations for user number 2580364
            games     score
0       Wolf Gold  0.395060
1  Fire Lightning  0.319082
2  Azrabah Wishes  0.258929
-------------
Recommendations for user number 2580604
                ga